In [7]:
import scripts.stock_plots as stock_plots
import scripts.stock_analysis as stock_ana
import plotly.graph_objects as go

from datetime import datetime, timedelta
import pandas as pd
import numpy as np
import yfinance as yf

import requests
from bs4 import BeautifulSoup

pd.set_option('mode.chained_assignment', None)  # Ignore the warning

In [10]:
url = "https://www.tradingview.com/markets/stocks-usa/market-movers-active/"
response = requests.get(url)
soup = BeautifulSoup(response.content, "html.parser")

In [12]:
response = requests.get(url)
soup = BeautifulSoup(response.content, 'html.parser')
table = soup.find('table')


In [13]:
data = pd.DataFrame(columns=['Ticker', 'Vol*Price (M)', 'Market cap (M)', "change"])


if response.status_code == 200:
    # Parse the HTML content of the webpage
    soup = BeautifulSoup(response.content, 'html.parser')

    # Find the table element on the webpage (you need to inspect the webpage to find the specific HTML tags)
    table = soup.find('table')  # Example: finding the first table on the page

    # Check if the table element was found
    if table:
        # Extract the table rows
        rows = table.find_all('tr')

        # Loop through each row and extract the data
        for row in rows:

            ticker_cell = row.find('td', class_='cell-RLhfr_y4')
            if ticker_cell:
              ticker_symbol = ticker_cell.find('a', class_='tickerName-GrtoTeat').text.strip()
              # print(ticker_symbol)


              value_1_cell = row.find_all('td')[1]
              chg_cell = row.find_all('td')[3]
              value_2_cell = row.find_all('td')[6]

              value_1 = value_1_cell.text.strip().split()
              chg_val = chg_cell.text.strip()
              value_2 = value_2_cell.text.strip().split()


              if len(value_1) == len(value_2):
                def to_million(extract):
                  if extract[1] == "T":
                    return float(extract[0]) * 1e6
                  elif extract[1] == "B":
                    return float(extract[0]) * 1e3
                  else:
                    return float(extract[0])

                vol_price = to_million(value_1)
                market_cap = to_million(value_2)


                if chg_val[0] == "+":
                  chg = float(chg_val[1:-1])
                else:
                  chg = -float(chg_val[1:-1])

                if market_cap < 2000:
                  pass
                else:
                  # print(vol_price, market_cap, relative_active)
                  data.loc[len(data.index)] = [ticker_symbol, vol_price, market_cap, chg]


                  # data = data.append({'Ticker': ticker_symbol, 'Vol*Price (M)': vol_price, 'Market cap (M)': market_cap, "relative_active": relative_active}, ignore_index=True)
                  # data = pd.concat([ticker_symbol, vol_price, market_cap, relative_active], ignore_index=True)

    else:
        print("Table element not found on the webpage.")
else:
    print("Failed to retrieve webpage. Status code:", response.status_code)

In [14]:
data["Ticker"]

0     NVDA
1     TSLA
2     AAPL
3      AMD
4     AMZN
      ... 
95    ORCL
96     MDT
97    KLAC
98    SHOP
99    REGN
Name: Ticker, Length: 100, dtype: object

In [2]:
def download_data(stocks):
    stocks_str = " ".join(stocks)
    return yf.Tickers(stocks_str)

In [3]:
big = ["SMCI", "AAPL", "GOOG", "AMZN"]
stock_data = download_data(big)



In [19]:
# selected = "0050.TW"

big = ["LULU", "SMCI", "AAPL", "GOOG", "AMZN"]

# big = data["Ticker"].head(10)

stock_data = download_data(big)



for selected in big:
    stock_plot = stock_plots.PlotInfo(stock_data.tickers[selected], selected, "400d")
    candle = stock_plot.generate_candle_plot(p2p_order=4)
    candle.show()

In [31]:
op_dates = stock_data.tickers[selected].options


call_chain = stock_data.tickers[selected].option_chain(op_dates[3]).calls
idx = sum(call_chain["inTheMoney"]) - 1

put_chain = stock_data.tickers[selected].option_chain(op_dates[3]).puts
idxp = -sum(put_chain["inTheMoney"])

# print(call_chain.iloc[idx-1], put_chain.iloc[-idxp])

call_chain.iloc[idx-5:idx+5]

contractSymbol             lastTradeDate  strike  lastPrice    bid  \
6   AAPL240510C00150000 2024-04-12 15:07:37+00:00   150.0      26.53  27.10   
7   AAPL240510C00155000 2024-04-12 18:13:59+00:00   155.0      21.95  22.35   
8   AAPL240510C00160000 2024-04-12 19:32:48+00:00   160.0      17.65  17.85   
9   AAPL240510C00165000 2024-04-12 19:41:40+00:00   165.0      13.30  13.50   
10  AAPL240510C00170000 2024-04-12 19:49:52+00:00   170.0       9.60   9.65   
11  AAPL240510C00175000 2024-04-12 19:57:12+00:00   175.0       6.51   6.45   
12  AAPL240510C00180000 2024-04-12 19:59:30+00:00   180.0       4.00   3.95   
13  AAPL240510C00185000 2024-04-12 19:58:59+00:00   185.0       2.32   2.30   
14  AAPL240510C00190000 2024-04-12 19:59:35+00:00   190.0       1.31   1.22   
15  AAPL240510C00195000 2024-04-12 19:59:10+00:00   195.0       0.67   0.65   

      ask    change  percentChange  volume  openInterest  impliedVolatility  \
6   27.90  1.440001       5.739341     5.0            11           0.511968   
7   23.00  3.650002      19.945364     4.0            24           0.445928   
8   18.15  1.150000       6.969695    57.0           119           0.381476   
9   13.80  1.040000       8.482870   174.0           460           0.348029   
10   9.85  1.150001      13.609475   400.0           999           0.320075   
11   6.60  1.160000      21.682250  1825.0          2983           0.303718   
12   4.15  0.890000      28.617367  5331.0          3785           0.295295   
13   2.35  0.670000      40.606056  2079.0          2301           0.285041   
14   1.30  0.430000      48.863632  2224.0          3607           0.284431   
15   0.73  0.240000      55.813957  2285.0          2542           0.290534   

    inTheMoney contractSize currency  
6         True      REGULAR      USD  
7         True      REGULAR      USD  
8         True      REGULAR      USD  
9         True      REGULAR      USD  
10        True      REGULAR      USD  
11        True      REGULAR      USD  
12       False      REGULAR      USD  
13       False      REGULAR      USD  
14       False      REGULAR      USD  
15       False      REGULAR      USD

In [117]:
def multi_forecast(df, days):
    df["priceRange"] = df.impliedVolatility * df.strike * np.sqrt(days/365)
    df["upper"] = (df.strike + df.priceRange).astype(int)
    df["lower"] = (df.strike - df.priceRange).astype(int)
    return df

def multi_op_chain(op_chain, days):
    op_chain = op_chain[op_chain.openInterest > op_chain.openInterest.mean()]
    op_chain = multi_forecast(op_chain, days)
    
    # range_analysis = np.zeros(op_chain.upper.max() + 1)
    range_analysis = np.zeros(220)

    for _, row in op_chain.iterrows():
        range_analysis[row.lower:row.upper] += 1


    # Create a bar chart
    fig = go.Figure(data=go.Bar(y=range_analysis))

    # Update layout
    fig.update_layout(
        title='Bar Chart',
        xaxis=dict(title='Category'),
        yaxis=dict(title='Value')
    )

    # fig.update_xaxes(range=[120, len(range_analysis)])  # Assuming x values are indices starting from 0


    # Show plot
    fig.show()

    return range_analysis


In [121]:
h = np.array([1,2,7,8,3,7,2,5,8,7,6,2])
np.where(h == 7)

(array([2, 5, 9], dtype=int64),)

In [118]:
def std_cal(strike, iv, days):
    std = iv * strike * np.sqrt(days/365)
    return strike+std, strike-std

strike = call_chain.iloc[idx-1]["strike"]
iv = call_chain.iloc[idx-1]["impliedVolatility"]
days = (datetime.strptime(op_dates[1], '%Y-%m-%d') - datetime.now()).days

In [120]:
selected = "AAPL"


for i in [1,2,3]:
    days = (datetime.strptime(op_dates[i], '%Y-%m-%d') - datetime.now()).days

    callop = multi_op_chain(stock_data.tickers[selected].option_chain(op_dates[i]).calls, days)
    putop = multi_op_chain(stock_data.tickers[selected].option_chain(op_dates[i]).puts, days)

    comb = putop + callop
    fig = go.Figure(data=go.Bar(y=comb))

    # Update layout
    fig.update_layout(
        title='Bar Chart',
        xaxis=dict(title='Category'),
        yaxis=dict(title='Value')
    )

    # fig.update_xaxes(range=[120, len(comb)])  # Assuming x values are indices starting from 0


    # Show plot
    fig.show()

    std_cal(strike, iv, days)

In [75]:
def std_cal(strike, iv, days):
    std = iv * strike * np.sqrt(days/365)
    return strike+std, strike-std

In [76]:
strike = call_chain.iloc[idx-1]["strike"]
iv = call_chain.iloc[idx-1]["impliedVolatility"]
days = (datetime.strptime(op_dates[1], '%Y-%m-%d') - datetime.now()).days
std_cal(strike, iv, days)

(184.22695384017518, 165.77304615982482)

In [77]:
up = []
low = []
date = [datetime.now()]
for i in [0,1,2,3,4,5,6]:
    tick = selected
    call_chain = stock_data.tickers[tick].option_chain(op_dates[i]).calls
    idx = sum(call_chain["inTheMoney"]) - 1
    strike = call_chain.iloc[idx]["strike"]
    iv = call_chain.iloc[idx]["impliedVolatility"]
    days = (datetime.strptime(op_dates[i], '%Y-%m-%d') - datetime.now()).days
    # print(strike, iv, days)
    # std_cal(strike, iv, days)

    put_chain = stock_data.tickers[tick].option_chain(op_dates[i]).puts
    idx1 = -sum(put_chain["inTheMoney"])
    strike1 = put_chain.iloc[idx1]["strike"]
    iv1 = put_chain.iloc[idx1]["impliedVolatility"]
    # print(strike1, iv1, days)
    # std_cal(strike1, iv1, days)

    strike = (strike + strike1) / 2
    iv = (iv + iv1) / 2
    # print(strike, iv, days)
    # std_cal(strike, iv, days)
    # print("-")

    ans = std_cal(strike, iv, days)

    
    if not up:
        # date.append(date.append(op_dates[i]))
        up.append(strike)
        low.append(strike)

    date.append(op_dates[i])
    up.append(ans[0])
    low.append(ans[1])


In [78]:
# Create line plots
trace1 = go.Scatter(x=date, y=up, mode='lines', name='Line 1')
trace2 = go.Scatter(x=date, y=low, mode='lines', name='Line 2')

# Create figure and add traces
fig = go.Figure([trace1, trace2])

# Update layout
fig.update_layout(
    title='Two Line Plots',
    xaxis=dict(title='X-axis Title'),
    yaxis=dict(title='Y-axis Title')
)

# Show plot
fig.show()

In [79]:
# candle

candle.add_trace(go.Scatter(x=date, y=up, mode='lines', name='upper'), row=1, col=1)
candle.add_trace(go.Scatter(x=date, y=low, mode='lines', name='lower'), row=1, col=1)

In [12]:
stock_price.index[-1]

Timestamp('2024-04-12 00:00:00-0400', tz='America/New_York')

In [140]:
def std_cal(strike, iv, days):
    std = iv * strike * np.sqrt(days/365)
    return strike+std, strike-std

big = ["SMCI", "AAPL", "GOOG", "AMZN", "TSLA", "AI"]
stock_data = download_data(big)
op_dates = stock_data.tickers[selected].options

for selected in big:
    stock_price = stock_data.tickers[selected].history(period=f"400d")

    stock_plot = stock_plots.PlotInfo(stock_price)
    candle = stock_plot.generate_candle_plot(p2p_order=4)
    candle.update_layout(title={"text": selected})

    up = []
    low = []
    date = []
    for i in [0,1,2,3,4,5,6]:
        tick = selected
        call_chain = stock_data.tickers[tick].option_chain(op_dates[i]).calls
        idx = sum(call_chain["inTheMoney"]) - 1
        strike = call_chain.iloc[idx]["strike"]
        iv = call_chain.iloc[idx]["impliedVolatility"]
        days = (datetime.strptime(op_dates[i], '%Y-%m-%d') - datetime.now()).days
        # print(strike, iv, days)
        # std_cal(strike, iv, days)

        put_chain = stock_data.tickers[tick].option_chain(op_dates[i]).puts
        idx1 = -sum(put_chain["inTheMoney"])
        strike1 = put_chain.iloc[idx1]["strike"]
        iv1 = put_chain.iloc[idx1]["impliedVolatility"]
        # print(strike1, iv1, days)
        # std_cal(strike1, iv1, days)

        strike = (strike + strike1) / 2
        iv = (iv + iv1) / 2
        # print(strike, iv, days)
        # std_cal(strike, iv, days)
        # print("-")

        ans = std_cal(strike, iv, days)

        
        if not up:
            # date.append(date.append(op_dates[i]))
            up.append(strike)
            low.append(strike)
            date.append(stock_price.index[-1])
            

        date.append(op_dates[i])
        up.append(ans[0])
        low.append(ans[1])
    
    candle.add_trace(go.Scatter(x=date, y=up, mode='lines+markers', name='pred'), row=1, col=1)
    candle.add_trace(go.Scatter(x=date, y=low, mode='lines+markers', showlegend=False), row=1, col=1)

    candle.update_layout(xaxis=dict(rangebreaks=[dict(bounds=["sat", "mon"])]))

    candle.show()

In [143]:
def std_cal(strike, iv, days):
    std = iv * strike * np.sqrt(days/365)
    return strike+std, strike-std

def multi_forecast(df, days):
    df["priceRange"] = df.impliedVolatility * df.strike * np.sqrt(days/365)
    df["upper"] = (df.strike + df.priceRange).astype(int)
    df["lower"] = (df.strike - df.priceRange).astype(int)
    return df

def range_collection(op_chain):
    range_analysis = np.zeros(2000)

    for _, row in op_chain.iterrows():
        range_analysis[row.lower:row.upper] += 1
    
    range_idx = np.where(range_analysis == (np.max(range_analysis) - 1))
    return range_idx

big = ["SMCI", "AAPL", "GOOG", "AMZN", "TSLA", "AI"]
stock_data = download_data(big)
op_dates = stock_data.tickers[selected].options

for selected in big:
    stock_price = stock_data.tickers[selected].history(period=f"400d")

    stock_plot = stock_plots.PlotInfo(stock_price)
    candle = stock_plot.generate_candle_plot(p2p_order=4)
    candle.update_layout(title={"text": selected})

    forecast = {"iv_upper": [],
                        "iv_lower": [],
                        "call_upper": [],
                        "call_lower": [],
                        "put_upper": [],
                        "put_lower": []}

    # up = []
    # low = []
    date = []
    for i in [0,1,2,3,4,5]:
        tick = selected
        days = (datetime.strptime(op_dates[i], '%Y-%m-%d') - datetime.now()).days

        call_chain = stock_data.tickers[tick].option_chain(op_dates[i]).calls
        idx = sum(call_chain["inTheMoney"]) - 1
        strike = call_chain.iloc[idx]["strike"]
        iv = call_chain.iloc[idx]["impliedVolatility"]

        call_chain = call_chain[call_chain.openInterest > call_chain.openInterest.mean()]
        call_chain = multi_forecast(call_chain, days)
        range_idx = range_collection(call_chain)
        
        
        
        put_chain = stock_data.tickers[tick].option_chain(op_dates[i]).puts
        idx1 = -sum(put_chain["inTheMoney"])
        strike1 = put_chain.iloc[idx1]["strike"]
        iv1 = put_chain.iloc[idx1]["impliedVolatility"]

        put_chain = put_chain[put_chain.openInterest > put_chain.openInterest.mean()]
        put_chain = multi_forecast(put_chain, days)
        range_idx1 = range_collection(put_chain)
        

        strike = (strike + strike1) / 2
        iv = (iv + iv1) / 2
        ans = std_cal(strike, iv, days)

        
        if i == 0:
            # date.append(date.append(op_dates[i]))
            # up.append(strike)
            # low.append(strike)
            date.append(stock_price.index[-1])
            forecast = {"iv_upper": [strike],
                        "iv_lower": [strike],
                        "call_upper": [strike],
                        "call_lower": [strike],
                        "put_upper": [strike],
                        "put_lower": [strike]}
            

        date.append(op_dates[i])
        forecast["iv_upper"].append(ans[0])
        forecast["iv_lower"].append(ans[1])
        forecast["call_upper"].append(np.max(range_idx))
        forecast["call_lower"].append(np.min(range_idx))
        forecast["put_upper"].append(np.max(range_idx1))
        forecast["put_lower"].append(np.min(range_idx1))
        # up.append(ans[0])
        # low.append(ans[1])
    
    candle.add_trace(go.Scatter(x=date, y=forecast["iv_upper"], mode='lines+markers', line_color="grey", name='pred'), row=1, col=1)
    candle.add_trace(go.Scatter(x=date, y=forecast["iv_lower"], mode='lines+markers', line_color="grey", showlegend=False), row=1, col=1)
    candle.add_trace(go.Scatter(x=date, y=forecast["call_upper"], mode='lines+markers', line_color="green", name='call'), row=1, col=1)
    candle.add_trace(go.Scatter(x=date, y=forecast["call_lower"], mode='lines+markers', line_color="green", showlegend=False), row=1, col=1)
    candle.add_trace(go.Scatter(x=date, y=forecast["put_upper"], mode='lines+markers', line_color="red", name='put'), row=1, col=1)
    candle.add_trace(go.Scatter(x=date, y=forecast["put_lower"], mode='lines+markers', line_color="red", showlegend=False), row=1, col=1)

    candle.update_layout(xaxis=dict(rangebreaks=[dict(bounds=["sat", "mon"])]))

    candle.show()
    # print(forecast)

In [135]:
forecast

{'iv_upper': [46.25,
  55.409935179097914,
  39.50537350624855,
  31.768597563380382,
  30.926222732421444,
  37.99592618909125,
  26.486861637554846],
 'iv_lower': [46.25,
  37.090064820902086,
  24.494626493751447,
  23.231402436619618,
  22.073777267578556,
  24.504073810908753,
  17.513138362445154],
 'call_upper': [46.25, 42, 33, 27, 28, 35, 30],
 'call_lower': [46.25, 23, 28, 25, 23, 26, 23],
 'put_upper': [46.25, 45, 24, 24, 24, 28, 26],
 'put_lower': [46.25, 16, 20, 21, 19, 21, 19]}